# Data Mining ⛏

**Purpose:** Collect all relevant Tweet's pertaining to the reopening of schools in the COVID-19 pandemic between Jan. 1, 2020 and Sept. 15, 2020.

**Pipeline:**
1. Connect to Twitter's Search Tweets API, to the `full archive` endpoint
2. Go province by province<sup>1</sup> and:
    1. Collect all tweets that mention that an education minister
    2. Collect all tweets that contain a dedicated list of keywords/hashtags
3. Store collection of tweets in Pandas dataframe, and only keep relevant features (data, geocode, text, author, *etc.*)
4. Add an extra column that is the cleaned tweet text.
5. Save dataframe to CSV
6. Solve the pandemic 🎊


<sup>1</sup> For more information on what tweets are geocoded, see [Twitter's geofiltering guide](https://developer.twitter.com/en/docs/tutorials/filtering-tweets-by-location)

In [1]:
import pandas as pd
import numpy as np
from searchtweets import collect_results, gen_rule_payload, load_credentials, ResultStream

premium_search_args = load_credentials(filename="../secrets/new_secret.yaml",yaml_key="search_tweets_api",env_overwrite=False)


Grabbing bearer token from OAUTH


## Location Filtering Rules

**Query Rules:** Each aspect of the query (mentions, keywords, hashtags, geo, etc...) should be encapsulated in their own brackets. Each part of the query, *aside from geo*, only needs one part to be satisfied, so those are all ORed together. Since geo must be satisfied, the rest of the query is put in brackets and geo is appended at the end.

**IMPORTANT** This does not work with the `sandbox` API tier so we need to pony up for `premium` first.

To collect tweets from province $X$, search for tweets where the account profile has location containing $X$ **OR** geocoded tweets that fall in $X$ 

Note: the `geo` attribute is deprecated and is ignored accordingly. For geocoded tweets only the `place` attribute will be used.

In [3]:
# has geo AND one of these place markers
country = '((has:geo OR has:profile_geo) (place_country:CA OR profile_country:CA))'

#### Keyword Strategy

3 conditions that a tweet must satisfy
1. It needs to be about the covid-19 pandemic (covid OR covid-19 OR coronavirus OR pandemic OR lockdown)
2. It needs to be about children/parental anxiety (child OR children OR kid OR LO OR toddler OR parent OR family)
3. It needs to be about school/the back to school season (school OR risk OR open OR reopen OR safe OR safety OR safely, etc..)

In [4]:
covid_filters = ["covid",
                 "covid-19",
                 "coronavirus",
                 "pandemic",
                 "lockdown",
                 "closure",
                 "virus"]

covid_filters = "(("+") OR (".join(covid_filters)+"))"

child_filters = ["child",
                 "children",
                 "toddler",
                 "kid",
                 "parent",
                 "family"]

child_filters = "(("+") OR (".join(child_filters)+"))"

school_filters = ["school",
          "schools",
          "preschools",
          "preschool",
          "daycare",
          "class",
          "classroom",
          "risk",
          "reopen",
          "return",
          "safe",
          "safety",
          "safely",
          "(online OR distance) learning",
          "daycare",
          "childcare"]

school_filters = "(("+") OR (".join(school_filters)+"))"

keywords = "("+" ".join([covid_filters,child_filters,school_filters])+")"
keywords


'(((covid) OR (covid-19) OR (coronavirus) OR (pandemic) OR (lockdown) OR (closure) OR (virus)) ((child) OR (children) OR (toddler) OR (kid) OR (parent) OR (family)) ((school) OR (schools) OR (preschools) OR (preschool) OR (daycare) OR (class) OR (classroom) OR (risk) OR (reopen) OR (return) OR (safe) OR (safety) OR (safely) OR ((online OR distance) learning) OR (daycare) OR (childcare)))'

#### Politician Matching Strategy

Must @ a politician (premier or education minister) and be pertinent to covid AND school reopenings

In [5]:
edu_minister_dict = {
    "AB": "@davideggenAB",
    "BC": "@Rob_Fleming",
    "MB": "@mingoertzen",
    "NB": "@DominicCardy",
    "NL": "@BrianWarr709",
    "NT": "@RJSimpson_NWT",
    "NS": "@zachchurchill",
    "ON": "@Sflecce",
    "PEI": "@bradtrivers",
    "QC": "@jfrobergeQc",
    "SK": "@GordWyant",
    "YT": "@TracyMcPheeRS"
}

premier_dict = {
    "AB": "@jkenney",
    "BC": "@jjhorgan",
    "MB": "@BrianPallister",
    "NB": "@blainehiggs",
    "NL": "@PremierofNL",
    "NT": "@CCochrane_NWT",
    "NS": "@StephenMcNeil",
    "NU": "@JSavikataaq",
    "ON": "@fordnation",
    "PEI": "@dennyking",
    "QC": "@francoislegault",
    "SK": "@PremierScottMoe",
    "YT": "@Premier_Silver"
}

politicians = " OR ".join([val for _,val in list(premier_dict.items())+list(edu_minister_dict.items())])

politicians = f"(({politicians}) ((covid OR covid-19) (school OR childcare OR daycare)))"
politicians


'((@jkenney OR @jjhorgan OR @BrianPallister OR @blainehiggs OR @PremierofNL OR @CCochrane_NWT OR @StephenMcNeil OR @JSavikataaq OR @fordnation OR @dennyking OR @francoislegault OR @PremierScottMoe OR @Premier_Silver OR @davideggenAB OR @Rob_Fleming OR @mingoertzen OR @DominicCardy OR @BrianWarr709 OR @RJSimpson_NWT OR @zachchurchill OR @Sflecce OR @bradtrivers OR @jfrobergeQc OR @GordWyant OR @TracyMcPheeRS) ((covid OR covid-19) (school OR childcare OR daycare)))'

In [6]:
hashtags = [
    '#safeseptember',
    '#unsafeseptember',
    '#backtoschool',
    '#BackToSchool2020'
]
hashtags = "("+" OR ".join(hashtags)+")"
hashtags


'(#safeseptember OR #unsafeseptember OR #backtoschool OR #BackToSchool2020)'

#### Sample Tweets

From: 
* March: 8, 20
* April: 8, 20
* May: 8, 20
* June: 8, 20
* July: 8, 20
* August: 8, 20
    

In [11]:
import os
import json


def create_query(filters,geo="",lang="en"):
    """
        Takes in a list of fully formed filters that can be satisfied in disjunction.
    """
    lang = f"lang:{lang}"
    filter_str = " OR ".join(filters)
    query = f"({filter_str}) {lang} {geo}"
    return query.strip()


def return_tweets(query,from_date,to_date):
    fp = "../data/raw_data/{}_{}.json".format(from_date,to_date)
    if os.path.isfile(fp):
        with open(fp) as fin:
            return json.load(fin),fp
    rule = gen_rule_payload(query,
                        from_date=from_date, #UTC 2018-10-21 00:00
                        to_date=to_date,
                        results_per_call=500)
    rs = ResultStream(rule_payload=rule,
                  max_pages=1,
#                   max_results=10**10,
                  **premium_search_args)
    tweets = list(rs.stream())
    with open(fp, 'w') as fout:
        json.dump(tweets,fout,indent=4)
    return tweets,fp

In [12]:
query = create_query([keywords,politicians,hashtags],country)
query


'((((covid) OR (covid-19) OR (coronavirus) OR (pandemic) OR (lockdown) OR (closure) OR (virus)) ((child) OR (children) OR (toddler) OR (kid) OR (parent) OR (family)) ((school) OR (schools) OR (preschools) OR (preschool) OR (daycare) OR (class) OR (classroom) OR (risk) OR (reopen) OR (return) OR (safe) OR (safety) OR (safely) OR ((online OR distance) learning) OR (daycare) OR (childcare))) OR ((@jkenney OR @jjhorgan OR @BrianPallister OR @blainehiggs OR @PremierofNL OR @CCochrane_NWT OR @StephenMcNeil OR @JSavikataaq OR @fordnation OR @dennyking OR @francoislegault OR @PremierScottMoe OR @Premier_Silver OR @davideggenAB OR @Rob_Fleming OR @mingoertzen OR @DominicCardy OR @BrianWarr709 OR @RJSimpson_NWT OR @zachchurchill OR @Sflecce OR @bradtrivers OR @jfrobergeQc OR @GordWyant OR @TracyMcPheeRS) ((covid OR covid-19) (school OR childcare OR daycare))) OR (#safeseptember OR #unsafeseptember OR #backtoschool OR #BackToSchool2020)) lang:en ((has:geo OR has:profile_geo) (place_country:CA OR 

In [38]:
query = create_query([keywords,politicians,hashtags],country)
from_date = "2020-08-17"
to_date = "2020-08-18"
tweets,fp = return_tweets(query,from_date=from_date,to_date=to_date)
print(fp)
tweets

../data/raw_data/2020-08-17_2020-08-18.json


[{'created_at': 'Mon Aug 17 23:59:58 +0000 2020',
  'id': 1295510715185410056,
  'id_str': '1295510715185410056',
  'text': 'RT @ElemTeachersTO: Smaller class sizes to ensure a #SafeSeptember are achievable if the govt is willing to be flexible, says @jbrownETTPre…',
  'source': '<a href="http://twitter.com/download/iphone" rel="nofollow">Twitter for iPhone</a>',
  'truncated': False,
  'in_reply_to_status_id': None,
  'in_reply_to_status_id_str': None,
  'in_reply_to_user_id': None,
  'in_reply_to_user_id_str': None,
  'in_reply_to_screen_name': None,
  'user': {'id': 735736584,
   'id_str': '735736584',
   'name': 'luv2teech1',
   'screen_name': 'luv2teech1',
   'location': 'Vaughan, Ontario',
   'url': None,
   'description': 'Life is short. Live. Laugh. Love. Lots.. Wife, Mother, Daughter, teacher of Gr. 3/4 at TDSB; U of Guelph Grad, Eco-Friendly, Olympic Fan! #clearthelistCA',
   'translator_type': 'none',
   'derived': {'locations': [{'country': 'Canada',
      'country_code': '

## Process Tweets

Feature constructing, tweet cleaning, etc...

In [39]:
import re
from math import isnan

def clean_tweet(text,extended_tweet,retweeted_status=None):
    if retweeted_status and type(retweeted_status) is dict:
        retweeted_status = dict(retweeted_status)
        cleaned = clean_tweet(retweeted_status.get("text"),retweeted_status.get("extended_tweet"))[:-1]
        return (*cleaned,True)
    if pd.isna(extended_tweet):
        return clean_text(text), text, False
    to_dict = dict(extended_tweet)
    return clean_text(to_dict["full_text"]),to_dict["full_text"], False

rex = re.compile(r'<a.*?>(.*?)</a>',re.S|re.M)
def clean_source(source):
    match = rex.match(source)
    return match.groups()[0].strip()

clean_user = lambda x : x["screen_name"] if x["screen_name"] else None

def clean_entities(entities):
    hashtags = [h["text"] for h in entities["hashtags"]] if entities["hashtags"] else np.nan
    urls = [h["expanded_url"] for h in entities["urls"]] if entities["urls"] else np.nan
    mentions = [h["screen_name"] for h in entities["user_mentions"]] if entities["user_mentions"] else np.nan
    return hashtags,urls,mentions

def check_user(user):
    user = dict(user)
    if "derived" in user and "locations" in user["derived"]:
        loc = dict(user)["derived"]["locations"][0]
        long_lat = loc.get("geo").get("coordinates")
        city = loc.get("locality",np.nan)
        prov = loc.get("region",np.nan)
        loc_tup = (loc.get("locality",np.nan),loc.get("region",np.nan),*long_lat)
        return loc_tup
    return (np.nan,np.nan,np.nan,np.nan)
    
def clean_location(place,user):
    if place:
        place = dict(place)
        long_lat = place["bounding_box"]["coordinates"][0][0]
        split = [l.strip() for l in place["full_name"].split(",")]
        if len(split) == 2:
            return tuple(split+long_lat)
        ## AFAIK the only time there's more than 1 comma in a place field is when the place is labelled 'unorganized'
        elif len(split) > 2:
            user_loc = check_user(user)
            # If the tweet location object is having problems and we can derive a user location, do so.
            if not user_loc.count(np.nan):
                return user_loc
            return (np.nan,split[-1],*long_lat)
        else:
            user_loc = check_user(user)
            # If the tweet location object is having problems and we can derive a user location, do so.
            if not user_loc.count(np.nan):
                return user_loc
            return (split[0],np.nan,*long_lat)
    else:
        return check_user(user)
        

In [40]:
from text_cleaning import clean_text
clean_fp = "../data/processed_data/{}_{}.csv".format(from_date,to_date)
cov_tweets = pd.DataFrame(tweets)
cov_tweets = cov_tweets[['id','user','created_at', 'source', 'text','extended_tweet','retweeted_status','place','entities','favorite_count', 'retweet_count']].set_index("id")
# Get twitter handle from user
cov_tweets["screen_name"] = cov_tweets["user"].apply(clean_user)
# clean the tweet text
cov_tweets[["text","extended_tweet","is_retweet"]] = cov_tweets[["text","extended_tweet","retweeted_status"]].apply(lambda x: clean_tweet(*x),axis=1,result_type="expand")
cov_tweets = cov_tweets.rename({"text": "clean_text","extended_tweet":"original_text"},axis=1)
# Get the city/province from the location data
cov_tweets[["city","province","longitude","latitude"]] = cov_tweets[["place","user"]].apply(lambda x : clean_location(*x),axis=1,result_type="expand")
cov_tweets = cov_tweets.drop(["place","user"],axis=1)
# Through what medium did they post the tweet?
cov_tweets["source"] = cov_tweets["source"].apply(clean_source)
# Extract tweet entities (hashtags, linked urls, etc...)
cov_tweets[["hashtags","urls","mentions"]] = cov_tweets[["entities"]].apply(lambda x : clean_entities(x["entities"]),result_type="expand",axis=1)
cov_tweets = cov_tweets.drop("entities",axis=1)
cov_tweets = cov_tweets[["created_at","screen_name","source","clean_text","original_text","is_retweet","favorite_count","retweet_count","hashtags","urls","mentions","city","province","longitude","latitude"]]
cov_tweets.to_csv(clean_fp)
cov_tweets.head()


created_at      screen_name  \
id                                                                     
1295510715185410056  Mon Aug 17 23:59:58 +0000 2020       luv2teech1   
1295510678984372225  Mon Aug 17 23:59:49 +0000 2020  NicolasRobidoux   
1295510586218823680  Mon Aug 17 23:59:27 +0000 2020    JacksonLaurel   
1295510538739490818  Mon Aug 17 23:59:16 +0000 2020        ruckmaker   
1295510522381705222  Mon Aug 17 23:59:12 +0000 2020           maleve   

                                   source  \
id                                          
1295510715185410056    Twitter for iPhone   
1295510678984372225       Twitter Web App   
1295510586218823680      Twitter for iPad   
1295510538739490818       Twitter Web App   
1295510522381705222  Twitterrific for iOS   

                                                            clean_text  \
id                                                                       
1295510715185410056  [small, class, size, ensure, safeseptember, ac...   
1295510678984372225  [promise, move, school, board, service, center...   
1295510586218823680  [jkenney, fail, understand, failed, school, re...   
1295510538739490818  [v_macd, ont_dad, taxpayer, keep, school, clos...   
1295510522381705222  [attempt, return, child, classroom, turn, slow...   

                                                         original_text  \
id                                                                       
1295510715185410056  Smaller class sizes to ensure a #SafeSeptember...   
1295510678984372225  1) The #CAQ promised the move from school boar...   
1295510586218823680  What @jkenney and his gov fail to understand i...   
1295510538739490818  @V_MacD @ONT_Dad As a taxpayer, I'd be more th...   
1295510522381705222  "U.S. attempt to return children to the classr...   

                     is_retweet  favorite_count  retweet_count  \
id                                                               
1295510715185410056        True               0              0   
1295510678984372225        True               0              0   
1295510586218823680        True               0              0   
1295510538739490818       False               0              0   
1295510522381705222        True               0              0   

                            hashtags  \
id                                     
1295510715185410056  [SafeSeptember]   
1295510678984372225            [CAQ]   
1295510586218823680              NaN   
1295510538739490818              NaN   
1295510522381705222              NaN   

                                                                  urls  \
id                                                                       
1295510715185410056                                                NaN   
1295510678984372225                                                NaN   
1295510586218823680                                                NaN   
1295510538739490818  [https://twitter.com/i/web/status/129551053873...   
1295510522381705222                                                NaN   

                                     mentions      city province  longitude  \
id                                                                            
1295510715185410056          [ElemTeachersTO]   Vaughan  Ontario  -79.49827   
1295510678984372225           [juan_c_castro]  Montréal   Quebec  -73.58781   
1295510586218823680  [CraigCoolahan, jkenney]   Calgary  Alberta -114.08529   
1295510538739490818         [V_MacD, ONT_Dad]       NaN      NaN -113.64258   
1295510522381705222            [yaneerbaryam]   Toronto  Ontario  -79.41630   

                     latitude  
id                             
1295510715185410056  43.83610  
1295510678984372225  45.50884  
1295510586218823680  51.05011  
1295510538739490818  60.10867  
1295510522381705222  43.70011